# Retail Data Wrangling and Analytics with PySpark
We will be implementing the data analytics process using PySpark and the retail data, which has been loaded already through the csv file 'retail.csv'. It now sits on a DBFS table.  
For plotting and data visualization we will be using Docker's display diagrams.

In [0]:
# Let's load the data into a dataframe

retail_df = spark.read.table('hive_metastore.default.retail')
display(retail_df.limit(20))

invoice_no stock_code description quantity invoice_date unit_price customer_id country 558461 21932 SCANDINAVIAN PAISLEY PICNIC BAG 3 2011-06-29T15:03:00Z 1.65 13263 United Kingdom 558475 21530 DAIRY MAID TOASTRACK 1 2011-06-29T15:58:00Z 3.29 null United Kingdom 558461 21933 PINK VINTAGE PAISLEY PICNIC BAG 3 2011-06-29T15:03:00Z 1.65 13263 United Kingdom 558462 21533 RETROSPOT LARGE MILK JUG 2 2011-06-29T15:11:00Z 4.95 13982 United Kingdom 558462 20724 RED RETROSPOT CHARLOTTE BAG 20 2011-06-29T15:11:00Z 0.85 13982 United Kingdom 558462 20718 RED RETROSPOT SHOPPER BAG 10 2011-06-29T15:11:00Z 1.25 13982 United Kingdom 558462 85099B JUMBO BAG RED RETROSPOT 10 2011-06-29T15:11:00Z 2.08 13982 United Kingdom 558462 82482 WOODEN PICTURE FRAME WHITE FINISH 6 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 558462 21531 RED RETROSPOT SUGAR JAM BOWL 4 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 558462 21535 RED RETROSPOT SMALL MILK JUG 4 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 558462 22667 RECIPE BOX RETROSPOT 3 2011-06-29T15:11:00Z 2.95 13982 United Kingdom 558462 20914 SET/5 RED RETROSPOT LID GLASS BOWLS 2 2011-06-29T15:11:00Z 2.95 13982 United Kingdom 558462 21080 SET/20 RED RETROSPOT PAPER NAPKINS 10 2011-06-29T15:11:00Z 0.85 13982 United Kingdom 558462 22465 HANGING METAL STAR LANTERN 12 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 558462 22464 HANGING METAL HEART LANTERN 18 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 558462 21498 RED RETROSPOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 558462 21500 PINK POLKADOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 558462 21499 BLUE POLKADOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 558462 21889 WOODEN BOX OF DOMINOES 6 2011-06-29T15:11:00Z 1.25 13982 United Kingdom 558462 71143 SILVER BOOK MARK WITH BEADS 10 2011-06-29T15:11:00Z 0.85 13982 United Kingdom

In [0]:
# Let's inspect the data
# Notice which cols have negative values or nulls
from pyspark.sql.functions import col

print("Null values for customer_id column: ")
print(retail_df.filter(
  col('customer_id').isNull()
).count())

display(retail_df.describe())

Null values for customer_id column: 
243007


summary invoice_no stock_code description quantity unit_price customer_id country count 1067371 1067371 1062989 1067371 1067371 824364 1067371 mean 537608.1499316233 28350.201592689715 21848.25 9.9388984711033 4.6493877274213995 15324.63850435002 null stddev 26662.450446904888 17968.479697262945 922.9197780233488 172.7057940767504 123.55305872146295 1697.4644503793106 null min 489434 10002 DOORMAT UNION JACK GUNS AND ROSES -80995 -53594.36 12346 Australia max C581569 m wrongly sold sets 80995 38970.0 18287 West Indies

## Total Invoice amount Distributions
Let's find the distribution of total invoice amount for the entire dataset after and before outliers are removed.

### Before Outliers were removed

In [0]:
# Add transaction total column
retail_df = retail_df.withColumn('transaction_total', retail_df.quantity * retail_df.unit_price)
display(retail_df.limit(50))

invoice_no stock_code description quantity invoice_date unit_price customer_id country transaction_total 558461 21932 SCANDINAVIAN PAISLEY PICNIC BAG 3 2011-06-29T15:03:00Z 1.65 13263 United Kingdom 4.949999999999999 558475 21530 DAIRY MAID TOASTRACK 1 2011-06-29T15:58:00Z 3.29 null United Kingdom 3.29 558461 21933 PINK VINTAGE PAISLEY PICNIC BAG 3 2011-06-29T15:03:00Z 1.65 13263 United Kingdom 4.949999999999999 558462 21533 RETROSPOT LARGE MILK JUG 2 2011-06-29T15:11:00Z 4.95 13982 United Kingdom 9.9 558462 20724 RED RETROSPOT CHARLOTTE BAG 20 2011-06-29T15:11:00Z 0.85 13982 United Kingdom 17.0 558462 20718 RED RETROSPOT SHOPPER BAG 10 2011-06-29T15:11:00Z 1.25 13982 United Kingdom 12.5 558462 85099B JUMBO BAG RED RETROSPOT 10 2011-06-29T15:11:00Z 2.08 13982 United Kingdom 20.8 558462 82482 WOODEN PICTURE FRAME WHITE FINISH 6 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 15.299999999999999 558462 21531 RED RETROSPOT SUGAR JAM BOWL 4 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 10.2 558462 21535 RED RETROSPOT SMALL MILK JUG 4 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 10.2 558462 22667 RECIPE BOX RETROSPOT 3 2011-06-29T15:11:00Z 2.95 13982 United Kingdom 8.850000000000001 558462 20914 SET/5 RED RETROSPOT LID GLASS BOWLS 2 2011-06-29T15:11:00Z 2.95 13982 United Kingdom 5.9 558462 21080 SET/20 RED RETROSPOT PAPER NAPKINS 10 2011-06-29T15:11:00Z 0.85 13982 United Kingdom 8.5 558462 22465 HANGING METAL STAR LANTERN 12 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 19.799999999999997 558462 22464 HANGING METAL HEART LANTERN 18 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 29.7 558462 21498 RED RETROSPOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 10.5 558462 21500 PINK POLKADOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 10.5 558462 21499 BLUE POLKADOT WRAP 25 2011-06-29T15:11:00Z 0.42 13982 United Kingdom 10.5 558462 21889 WOODEN BOX OF DOMINOES 6 2011-06-29T15:11:00Z 1.25 13982 United Kingdom 7.5 558462 71143 SILVER BOOK MARK WITH BEADS 10 2011-06-29T15:11:00Z 0.85 13982 United Kingdom 8.5 558462 22561 WOODEN SCHOOL COLOURING SET 6 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 9.899999999999999 558462 17003 BROCADE RING PURSE 36 2011-06-29T15:11:00Z 0.29 13982 United Kingdom 10.44 558462 22079 RIBBON REEL HEARTS DESIGN 5 2011-06-29T15:11:00Z 1.65 13982 United Kingdom 8.25 558462 85123A WHITE HANGING HEART T-LIGHT HOLDER 32 2011-06-29T15:11:00Z 2.55 13982 United Kingdom 81.6 C558463 84029E RED WOOLLY HOTTIE WHITE HEART. -1 2011-06-29T15:14:00Z 3.95 13982 United Kingdom -3.95 C558463 21535 RED RETROSPOT SMALL MILK JUG -1 2011-06-29T15:14:00Z 2.55 13982 United Kingdom -2.55 C558463 21531 RED RETROSPOT SUGAR JAM BOWL -1 2011-06-29T15:14:00Z 2.55 13982 United Kingdom -2.55 C558463 22464 HANGING METAL HEART LANTERN -1 2011-06-29T15:14:00Z 1.65 13982 United Kingdom -1.65 558464 35966 null -20 2011-06-29T15:17:00Z 0.0 null United Kingdom -0.0 C558465 22729 ALARM CLOCK BAKELIKE ORANGE -1 2011-06-29T15:19:00Z 3.75 13418 United Kingdom -3.75 C558466 21110 LARGE CAKE TOWEL PINK SPOTS -2 2011-06-29T15:20:00Z 6.75 12951 United Kingdom -13.5 558467 22690 DOORMAT HOME SWEET HOME BLUE 1 2011-06-29T15:22:00Z 7.95 17757 United Kingdom 7.95 558467 22086 PAPER CHAIN KIT 50'S CHRISTMAS 10 2011-06-29T15:22:00Z 2.95 17757 United Kingdom 29.5 558467 22628 PICNIC BOXES SET OF 3 RETROSPOT 1 2011-06-29T15:22:00Z 4.95 17757 United Kingdom 4.95 558467 21528 DAIRY MAID TRADITIONAL TEAPOT 1 2011-06-29T15:22:00Z 6.95 17757 United Kingdom 6.95 558467 22624 IVORY KITCHEN SCALES 1 2011-06-29T15:22:00Z 8.5 17757 United Kingdom 8.5 558467 23243 SET OF TEA COFFEE SUGAR TINS PANTRY 6 2011-06-29T15:22:00Z 4.95 17757 United Kingdom 29.700000000000003 558467 23196 RETRO LEAVES MAGNETIC NOTEPAD 2 2011-06-29T15:22:00Z 1.45 17757 United Kingdom 2.9 558467 23198 PANTRY MAGNETIC SHOPPING LIST 3 2011-06-29T15:22:00Z 1.45 17757 United Kingdom 4.35 558467 23197 SKETCHBOOK MAGNETIC SHOPPING LIST 4 2011-06-29T15:22:00Z 1.45 17757 United Kingdom 5.8 55

In [0]:
# Remove rows where transaction total was negative
retail_df_invoice_amount = retail_df.filter(retail_df.transaction_total > 0)

# Remove special case invoices with letters - these are special cases like cancellations
retail_df_invoice_amount = retail_df_invoice_amount.filter(~retail_df_invoice_amount.invoice_no.rlike('[a-zA-Z]'))

display(retail_df_invoice_amount.limit(50))


invoice_no stock_code description quantity invoice_date unit_price customer_id country transaction_total 489434 85048 15CM CHRISTMAS GLASS BALL 20 LIGHTS 12 2009-12-01T07:45:00Z 6.95 13085 United Kingdom 83.4 489434 79323P PINK CHERRY LIGHTS 12 2009-12-01T07:45:00Z 6.75 13085 United Kingdom 81.0 489434 79323W WHITE CHERRY LIGHTS 12 2009-12-01T07:45:00Z 6.75 13085 United Kingdom 81.0 489434 22041 RECORD FRAME 7" SINGLE SIZE 48 2009-12-01T07:45:00Z 2.1 13085 United Kingdom 100.80000000000001 489434 21232 STRAWBERRY CERAMIC TRINKET BOX 24 2009-12-01T07:45:00Z 1.25 13085 United Kingdom 30.0 489434 22064 PINK DOUGHNUT TRINKET POT 24 2009-12-01T07:45:00Z 1.65 13085 United Kingdom 39.599999999999994 489434 21871 SAVE THE PLANET MUG 24 2009-12-01T07:45:00Z 1.25 13085 United Kingdom 30.0 489434 21523 FANCY FONT HOME SWEET HOME DOORMAT 10 2009-12-01T07:45:00Z 5.95 13085 United Kingdom 59.5 489435 22350 CAT BOWL 12 2009-12-01T07:46:00Z 2.55 13085 United Kingdom 30.599999999999998 489435 22349 DOG BOWL , CHASING BALL DESIGN 12 2009-12-01T07:46:00Z 3.75 13085 United Kingdom 45.0 489435 22195 HEART MEASURING SPOONS LARGE 24 2009-12-01T07:46:00Z 1.65 13085 United Kingdom 39.599999999999994 489435 22353 LUNCHBOX WITH CUTLERY FAIRY CAKES 12 2009-12-01T07:46:00Z 2.55 13085 United Kingdom 30.599999999999998 489436 48173C DOOR MAT BLACK FLOCK 10 2009-12-01T09:06:00Z 5.95 13078 United Kingdom 59.5 489436 21755 LOVE BUILDING BLOCK WORD 18 2009-12-01T09:06:00Z 5.45 13078 United Kingdom 98.10000000000001 489436 21754 HOME BUILDING BLOCK WORD 3 2009-12-01T09:06:00Z 5.95 13078 United Kingdom 17.85 489436 84879 ASSORTED COLOUR BIRD ORNAMENT 16 2009-12-01T09:06:00Z 1.69 13078 United Kingdom 27.04 489436 22119 PEACE WOODEN BLOCK LETTERS 3 2009-12-01T09:06:00Z 6.95 13078 United Kingdom 20.85 489436 22142 CHRISTMAS CRAFT WHITE FAIRY 12 2009-12-01T09:06:00Z 1.45 13078 United Kingdom 17.4 489436 22296 HEART IVORY TRELLIS LARGE 12 2009-12-01T09:06:00Z 1.65 13078 United Kingdom 19.799999999999997 489436 22295 HEART FILIGREE DOVE LARGE 12 2009-12-01T09:06:00Z 1.65 13078 United Kingdom 19.799999999999997 489436 22109 FULL ENGLISH BREAKFAST PLATE 16 2009-12-01T09:06:00Z 3.39 13078 United Kingdom 54.24 489436 22107 PIZZA PLATE IN BOX 4 2009-12-01T09:06:00Z 3.75 13078 United Kingdom 15.0 489436 22194 BLACK DINER WALL CLOCK 2 2009-12-01T09:06:00Z 8.5 13078 United Kingdom 17.0 489436 35004B SET OF 3 BLACK FLYING DUCKS 12 2009-12-01T09:06:00Z 4.65 13078 United Kingdom 55.800000000000004 489436 82582 AREA PATROLLED METAL SIGN 12 2009-12-01T09:06:00Z 2.1 13078 United Kingdom 25.200000000000003 489436 21181 PLEASE ONE PERSON METAL SIGN 12 2009-12-01T09:06:00Z 2.1 13078 United Kingdom 25.200000000000003 489436 21756 BATH BUILDING BLOCK WORD 3 2009-12-01T09:06:00Z 5.95 13078 United Kingdom 17.85 489436 21333 CLASSIC WHITE FRAME 6 2009-12-01T09:06:00Z 2.95 13078 United Kingdom 17.700000000000003 489436 84596F SMALL MARSHMALLOWS PINK BOWL 8 2009-12-01T09:06:00Z 1.25 13078 United Kingdom 10.0 489436 84596L BISCUITS SMALL BOWL LIGHT BLUE 8 2009-12-01T09:06:00Z 1.25 13078 United Kingdom 10.0 489436 22111 SCOTTIE DOG HOT WATER BOTTLE 24 2009-12-01T09:06:00Z 4.25 13078 United Kingdom 102.0 489437 22143 CHRISTMAS CRAFT HEART DECORATIONS 6 2009-12-01T09:08:00Z 2.1 15362 United Kingdom 12.600000000000001 489437 22145 CHRISTMAS CRAFT HEART STOCKING 6 2009-12-01T09:08:00Z 2.1 15362 United Kingdom 12.600000000000001 489437 22130 PARTY CONE CHRISTMAS DECORATION 12 2009-12-01T09:08:00Z 0.85 15362 United Kingdom 10.2 489437 21364 PEACE SMALL WOOD LETTERS 2 2009-12-01T09:08:00Z 6.75 15362 United Kingdom 13.5 489437 21360 JOY LARGE WOOD LETTERS 1 2009-12-01T09:08:00Z 9.95 15362 United Kingdom 9.95 489437 21351 CINAMMON & ORANGE WREATH 2 2009-12-01T09:08:00Z 6.75 15362 United Kingdom 13.5 489437 21352 EUCALYPTUS & PINECONE WREATH 2 2009-12-01T09:08:00Z 6.75 15362 United Kingdom 13.5 489437 35400 WOODEN BOX ADVENT CALENDAR 2 2009-12-01T09:08:00Z 8.95 15362 United Kingdom 17.9 489437 20695 FLOR

In [0]:
# Find the median, mean, min, and max of invoice amount as well as show a distribution of the data
# Note that invoice amount is the total of all transactions for that invoice

from pyspark.sql.functions import col

invoice_values = retail_df_invoice_amount.select('invoice_no', 'transaction_total').groupBy('invoice_no').sum('transaction_total')
invoice_values = invoice_values.select(
  col('sum(transaction_total)').alias('invoice_values')
)

display(invoice_values)

invoice_values 192.0 303.2 155.05999999999997 118.75 275.95 6711.0 1335.92 2507.06 48.96 199.29999999999998 188.82999999999998 291.14000000000004 312.5899999999999 207.15000000000006 190.95000000000005 275.04 899.0 431.59000000000015 18.85 2655.96 11.9 612.0 270.9200000000001 1103.85 172.35 106.96000000000001 304.33 355.18999999999994 315.84999999999997 216.54 328.48 105.71 306.2 673.8599999999998 360.9000000000001 1621.7999999999997 207.35999999999999 60.0 112.94 160.4 100.8 4.25 30.499999999999993 180.65 270.04999999999995 65.05000000000001 511.0399999999999 319.6 298.55 433.97999999999996 765.0 333.6 185.46 313.94999999999993 135.46000000000004 162.24 273.96000000000004 130.64 73.09 271.38999999999993 406.26 311.38000000000005 147.2 141.60000000000002 157.70000000000002 1124.8 154.05 301.59999999999997 305.2 14.98 307.95000000000016 537.36 2154.1499999999996 99.5 7.6499999999999995 388.11999999999995 265.33 594.83 5245.18 357.18999999999994 17.55 2.55 153.33 591.85 139.31 96.45 312.71999999999997 242.3199999999999 3424.0800000000004 415.6600000000002 803.9999999999999 688.4000000000001 565.74 178.95 76.18 3361.76 52.699999999999996 621.14 458.91999999999985 320.28000000000003 338.9799999999999 403.79999999999995 751.0 365.2 169.35 919.9799999999998 158.95 2919.5099999999998 728.16 169.65 178.1 197.94000000000003 161.95000000000002 317.25 298.10999999999996 198.20000000000002 178.41 376.0 171.20000000000005 68.0 640.0 58.900000000000006 185.31 354.7999999999999 754.5499999999998 416.45 466.2799999999998 5410.0599999999995 293.0 554.4200000000001 112.19999999999999 305.36000000000007 181.1 613.9299999999998 12.64 320.48 296.32 48.4 360.07 213.79999999999998 474.86999999999995 53.91 624.1200000000001 100.67 411.3299999999999 485.7900000000001 597.6899999999999 176.87999999999997 54.599999999999994 869.9300000000001 933.35 533.9699999999999 263.67999999999995 504.53999999999996 208.83 10.0 404.82 124.89999999999999 485.40000000000003 212.0 953.5000000000006 228.96 299.52000000000004 367.6 268.67999999999995 205.56 144.35000000000002 146.68 271.05 222.11 332.37 359.83 142.8 135.55 595.54 211.15000000000003 454.15 837.1100000000001 1926.4 136.70000000000002 610.34 245.47999999999993 233.04999999999998 247.19000000000003 109.54000000000002 428.6799999999999 153.35999999999999 155.21 340.57 291.33 275.84000000000003 161.4 395.1 368.2 306.78000000000003 660.0 128.31 478.08000000000004 431.71999999999997 277.89 305.71999999999997 140.54000000000002 470.3 187.9 183.48000000000002 633.25 957.9800000000002 34.849999999999994 13.85 247.65000000000003 601.3199999999999 375.50000000000006 1735.4099999999996 395.68999999999994 1.25 222.16000000000003 12.600000000000001 238.74999999999997 104.80000000000001 407.7899999999999 175.60000000000002 791.22 653.2500000000005 271.27 110.77000000000001 178.3 503.4 1155.6 210.28999999999996 299.48 470.7299999999999 127.34 234.85 875.8100000000003 142.8 211.92000000000002 174.9 405.58 103.34 540.0 224.5 163.1500000000001 300.07000000000005 300.65000000000003 204.76999999999998 205.57999999999998 76.2 34.8 6272.010000000006 363.24 58.7 327.59999999999997 119.30000000000001 289.5 581.66 455.0199999999999 48.22 79.2 395.09999999999997 169.94 161.5 314.96000000000004 300.19 1191.7099999999998 316.85 585.12 174.16000000000003 137.4 433.9 198.89999999999998 180.38000000000002 127.84000000000002 275.1 252.53 50.0 313.79999999999995 81.6 4390.560000000002 593.52 99.6 243.51999999999995 358.20000000000005 270.0 304.58 227.57999999999998 472.0899999999999 2026.6299999999999 183.26 452.0 469.0 314.7 3096.0 321.96000000000004 148.95999999999998 87.89999999999999 392.4 135.0 278.33999999999986 263.09000000000003 301.88000000000005 146.61 325.26 542.7 184.82 382.46 282.46000000000004 870.28 183.59999999999997 34.0 4.25 135.94000000000003 97.55 343.52000000000004 334.5 194.1 164.34000000000003 588.4499999999999 302.4 107.14 77.52 305.4 136.93 109.59 208.92000000000002 721.4599999999998 1083.0500000000006 525.33999999

Databricks data profile. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

We used Databrick's built-in visualization tools to show the distribution of invoice totals as well as the mean, median, min and max values. Important to note that the data in the boxplot, which also shows distribution of the values, was truncated to just 10K rows for performance reasons so it is a close estimation. The bar graph in the Data Profile is a more accurate representation.

### After outliers were removed

In [0]:
# Remove null values
invoice_values = invoice_values.dropna()
print(invoice_values.filter(invoice_values.invoice_values.isNull()).count())

# Find first 85 quantiles of the data
quantile = invoice_values.approxQuantile('invoice_values', [0.85], 0.0)[0]
invoice_values_85 = invoice_values.filter(col('invoice_values') <= quantile)

# Display data profile and graph as before
display(invoice_values_85)

0


invoice_values 192.0 303.2 155.05999999999997 118.75 275.95 48.96 199.29999999999998 188.82999999999998 291.14000000000004 312.5899999999999 207.15000000000006 190.95000000000005 275.04 431.59000000000015 18.85 11.9 612.0 270.9200000000001 172.35 106.96000000000001 304.33 355.18999999999994 315.84999999999997 216.54 328.48 105.71 306.2 673.8599999999998 360.9000000000001 207.35999999999999 60.0 112.94 160.4 100.8 4.25 30.499999999999993 180.65 270.04999999999995 65.05000000000001 511.0399999999999 319.6 298.55 433.97999999999996 333.6 185.46 313.94999999999993 135.46000000000004 162.24 273.96000000000004 130.64 73.09 271.38999999999993 406.26 311.38000000000005 147.2 141.60000000000002 157.70000000000002 154.05 301.59999999999997 305.2 14.98 307.95000000000016 537.36 99.5 7.6499999999999995 388.11999999999995 265.33 594.83 357.18999999999994 17.55 2.55 153.33 591.85 139.31 96.45 312.71999999999997 242.3199999999999 415.6600000000002 688.4000000000001 565.74 178.95 76.18 52.699999999999996 621.14 458.91999999999985 320.28000000000003 338.9799999999999 403.79999999999995 365.2 169.35 158.95 169.65 178.1 197.94000000000003 161.95000000000002 317.25 298.10999999999996 198.20000000000002 178.41 376.0 171.20000000000005 68.0 640.0 58.900000000000006 185.31 354.7999999999999 416.45 466.2799999999998 293.0 554.4200000000001 112.19999999999999 305.36000000000007 181.1 613.9299999999998 12.64 320.48 296.32 48.4 360.07 213.79999999999998 474.86999999999995 53.91 624.1200000000001 100.67 411.3299999999999 485.7900000000001 597.6899999999999 176.87999999999997 54.599999999999994 533.9699999999999 263.67999999999995 504.53999999999996 208.83 10.0 404.82 124.89999999999999 485.40000000000003 212.0 228.96 299.52000000000004 367.6 268.67999999999995 205.56 144.35000000000002 146.68 271.05 222.11 332.37 359.83 142.8 135.55 595.54 211.15000000000003 454.15 136.70000000000002 610.34 245.47999999999993 233.04999999999998 247.19000000000003 109.54000000000002 428.6799999999999 153.35999999999999 155.21 340.57 291.33 275.84000000000003 161.4 395.1 368.2 306.78000000000003 660.0 128.31 478.08000000000004 431.71999999999997 277.89 305.71999999999997 140.54000000000002 470.3 187.9 183.48000000000002 633.25 34.849999999999994 13.85 247.65000000000003 601.3199999999999 375.50000000000006 395.68999999999994 1.25 222.16000000000003 12.600000000000001 238.74999999999997 104.80000000000001 407.7899999999999 175.60000000000002 653.2500000000005 271.27 110.77000000000001 178.3 503.4 210.28999999999996 299.48 470.7299999999999 127.34 234.85 142.8 211.92000000000002 174.9 405.58 103.34 540.0 224.5 163.1500000000001 300.07000000000005 300.65000000000003 204.76999999999998 205.57999999999998 76.2 34.8 363.24 58.7 327.59999999999997 119.30000000000001 289.5 581.66 455.0199999999999 48.22 79.2 395.09999999999997 169.94 161.5 314.96000000000004 300.19 316.85 585.12 174.16000000000003 137.4 433.9 198.89999999999998 180.38000000000002 127.84000000000002 275.1 252.53 50.0 313.79999999999995 81.6 593.52 99.6 243.51999999999995 358.20000000000005 270.0 304.58 227.57999999999998 472.0899999999999 183.26 452.0 469.0 314.7 321.96000000000004 148.95999999999998 87.89999999999999 392.4 135.0 278.33999999999986 263.09000000000003 301.88000000000005 146.61 325.26 542.7 184.82 382.46 282.46000000000004 183.59999999999997 34.0 4.25 135.94000000000003 97.55 343.52000000000004 334.5 194.1 164.34000000000003 588.4499999999999 302.4 107.14 77.52 305.4 136.93 109.59 208.92000000000002 721.4599999999998 525.3399999999999 401.6499999999999 360.59999999999997 206.6600000000001 120.51000000000002 236.64 378.59999999999985 599.4399999999998 289.94 145.28 94.53 331.54999999999995 20.0 286.11999999999995 252.84 526.7099999999999 645.35 60.55 98.84 272.62 335.1800000000002 128.95000000000002 108.0 486.90000000000003 405.15000000000003 31.8 149.12000000000003 96.44000000000003 310.49 129.84000000000003 2.95 136.65 170.0 536.4099999999999 139.8 284.5 119.01000000000002 3.37 135.4 68.399999999999

Databricks data profile. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

## Monthly Place and Cancelled Orders

Important notes:
- Cancelled orders have a 'C' in their invoice number
- Assume cancelled orders and normal orders occured on same day
- Formula for number of placed orders is total_orders - 2*cancelled_orders

In [0]:
# Create yearmonth column
from pyspark.sql.functions import col, date_format

retail_df = retail_df.withColumn("year_month", date_format("invoice_date", "yyyyMM"))
display(retail_df.orderBy('year_month').limit(10))

invoice_no stock_code description quantity invoice_date unit_price customer_id country transaction_total year_month 489434 79323W WHITE CHERRY LIGHTS 12 2009-12-01T07:45:00Z 6.75 13085 United Kingdom 81.0 200912 489434 21232 STRAWBERRY CERAMIC TRINKET BOX 24 2009-12-01T07:45:00Z 1.25 13085 United Kingdom 30.0 200912 489434 85048 15CM CHRISTMAS GLASS BALL 20 LIGHTS 12 2009-12-01T07:45:00Z 6.95 13085 United Kingdom 83.4 200912 489434 22041 RECORD FRAME 7" SINGLE SIZE 48 2009-12-01T07:45:00Z 2.1 13085 United Kingdom 100.80000000000001 200912 489434 22064 PINK DOUGHNUT TRINKET POT 24 2009-12-01T07:45:00Z 1.65 13085 United Kingdom 39.599999999999994 200912 489434 79323P PINK CHERRY LIGHTS 12 2009-12-01T07:45:00Z 6.75 13085 United Kingdom 81.0 200912 489435 22350 CAT BOWL 12 2009-12-01T07:46:00Z 2.55 13085 United Kingdom 30.599999999999998 200912 489434 21523 FANCY FONT HOME SWEET HOME DOORMAT 10 2009-12-01T07:45:00Z 5.95 13085 United Kingdom 59.5 200912 489434 21871 SAVE THE PLANET MUG 24 2009-12-01T07:45:00Z 1.25 13085 United Kingdom 30.0 200912 489435 22349 DOG BOWL , CHASING BALL DESIGN 12 2009-12-01T07:46:00Z 3.75 13085 United Kingdom 45.0 200912

In [0]:
# Add column to tell us which rows are cancelled
from pyspark.sql.functions import col, when
from pyspark.sql.types import IntegerType

retail_df_monthly_orders = retail_df.dropDuplicates(['invoice_no']).withColumn(
  'cancelled_order',
  when(col('invoice_no').startswith('C'), 1).otherwise(0).cast(IntegerType())
)

display(retail_df_monthly_orders.limit(5))



invoice_no stock_code description quantity invoice_date unit_price customer_id country transaction_total year_month cancelled_order 489677 21341 KASBAH LANTERN WITH GLASS 24 2009-12-02T09:50:00Z 4.25 14000 United Kingdom 102.0 200912 0 C491017 85044 RED REINDEER STRING OF 20 LIGHTS -1 2009-12-08T18:38:00Z 4.95 13643 United Kingdom -4.95 200912 1 491045 71477 COLOUR GLASS. STAR T-LIGHT HOLDER 48 2009-12-09T10:02:00Z 2.75 12747 United Kingdom 132.0 200912 0 491658 85166A WHITE METAL BAROQUE PHOTO FRAME 1 2009-12-13T11:05:00Z 3.75 16442 United Kingdom 3.75 200912 0 C491705 84482 BUTTONS DESIGN JEWELLERY BOX -6 2009-12-13T14:09:00Z 3.75 17802 United Kingdom -22.5 200912 1

In [0]:
# Find number of cancelled orders and number of placed orders per month
retail_df_all_orders = retail_df_monthly_orders.select('invoice_no', 'year_month').groupBy('year_month').count()
retail_df_cancelled_orders = retail_df_monthly_orders.filter(col('cancelled_order') == 1).groupBy('year_month').count().withColumnRenamed('count', 'cancelled_count')

retail_df_monthly_placed_orders = retail_df_all_orders.join(retail_df_cancelled_orders, on='year_month', how='inner').withColumn('placed_count', col('count') - 2*col('cancelled_count'))

display(retail_df_monthly_placed_orders)

year_month count cancelled_count placed_count 201103 1983 318 1347 201001 1633 300 1033 201002 1969 240 1489 201010 2965 476 2013 201009 2375 371 1633 201104 1744 240 1264 201106 2012 329 1354 201102 1393 219 955 201110 2637 362 1913 201008 1877 273 1331 201107 1927 270 1387 201012 2025 326 1373 201105 2162 314 1534 201109 2327 333 1661 201011 3669 576 2517 201007 2017 344 1329 201111 3462 441 2580 201108 1737 278 1181 201112 1015 146 723 201004 1892 304 1284 200912 2330 401 1528 201006 2216 357 1502 201005 2418 407 1604 201101 1476 260 956 201003 2367 407 1553

Databricks visualization. Run in Databricks to view.

## Monthly Sales

In [0]:
retail_df_monthly_sales = retail_df.groupBy('year_month').sum('transaction_total').orderBy('year_month').withColumnRenamed('sum(transaction_total)', 'monthly_sales')

display(retail_df_monthly_sales)

year_month monthly_sales 200912 799847.1100000143 201001 624032.8919999955 201002 533091.4260000042 201003 765848.7609999765 201004 590580.4319999823 201005 615322.8300000005 201006 679786.6099999842 201007 575236.359999999 201008 656776.3399999854 201009 853650.4309999745 201010 1045168.3499998983 201011 1422654.6419998251 201012 1126445.4699999166 201101 560000.2600000234 201102 498062.65000002686 201103 683267.0800000189 201104 493207.1210000249 201105 723333.51000001 201106 691123.1200000229 201107 681300.1110000301 201108 682680.5100000179 201109 1019687.622000011 201110 1070704.6699999748 201111 1461756.2499997574 201112 433686.0100000171

Databricks visualization. Run in Databricks to view.

## Monthly Sales Growth

In [0]:
# Use a window function to shift year_month back by 1
from pyspark.sql.functions import col, lag
from pyspark.sql.window import Window

window_spec = Window.orderBy(col('year_month'))

retail_df_sales_growth = retail_df_monthly_sales.withColumn(
  'previous_month_sales', lag(col('monthly_sales')).over(window_spec)
)

retail_df_sales_growth = retail_df_sales_growth.withColumn(
  'sales_growth', col('monthly_sales') / col('previous_month_sales')
)

display(retail_df_sales_growth)




year_month monthly_sales previous_month_sales sales_growth 200912 799847.1100000143 null null 201001 624032.8919999955 799847.1100000143 0.7801902191032287 201002 533091.4260000042 624032.8919999955 0.8542681529037224 201003 765848.7609999765 533091.4260000042 1.4366180426994348 201004 590580.4319999823 765848.7609999765 0.7711449858962434 201005 615322.8300000005 590580.4319999823 1.0418950521544184 201006 679786.6099999842 615322.8300000005 1.1047641609526881 201007 575236.359999999 679786.6099999842 0.8462013689855004 201008 656776.3399999854 575236.359999999 1.1417503928298038 201009 853650.4309999745 656776.3399999854 1.2997581962224667 201010 1045168.3499998983 853650.4309999745 1.2243516925020208 201011 1422654.6419998251 1045168.3499998983 1.3611727163379599 201012 1126445.4699999166 1422654.6419998251 0.7917912308053011 201101 560000.2600000234 1126445.4699999166 0.49713925344301385 201102 498062.65000002686 560000.2600000234 0.8893971763513218 201103 683267.0800000189 498062.65000002686 1.3718496659004287 201104 493207.1210000249 683267.0800000189 0.7218365049872024 201105 723333.51000001 493207.1210000249 1.4665917810216968 201106 691123.1200000229 723333.51000001 0.9554695177885694 201107 681300.1110000301 691123.1200000229 0.9857868898959818 201108 682680.5100000179 681300.1110000301 1.00202612472492 201109 1019687.622000011 682680.5100000179 1.4936527512701134 201110 1070704.6699999748 1019687.622000011 1.0500320361836883 201111 1461756.2499997574 1070704.6699999748 1.3652282379601388 201112 433686.0100000171 1461756.2499997574 0.2966883226940806

Databricks visualization. Run in Databricks to view.

## Monthly Active Customers

In [0]:
from pyspark.sql.functions import countDistinct

retail_df_uniq_customers = retail_df.select('customer_id', 'year_month').groupBy("year_month").agg(
  countDistinct('customer_id').alias('uniq_customers')
)

display(retail_df_uniq_customers.orderBy('year_month'))

year_month uniq_customers 200912 1045 201001 786 201002 807 201003 1111 201004 998 201005 1062 201006 1095 201007 988 201008 964 201009 1202 201010 1577 201011 1683 201012 948 201101 783 201102 798 201103 1020 201104 899 201105 1079 201106 1051 201107 993 201108 980 201109 1302 201110 1425 201111 1711 201112 686

Databricks visualization. Run in Databricks to view.

## New and Existing Customer
Our Approach:
- An existing customer is one that already made a purchase in a previous month
- A new customer is one that makes their first purchase in that month

In [0]:
# Find first purchase month of each user
from pyspark.sql.functions import min, col

retail_df_first_purchase_month = retail_df.select(
  col('customer_id'),
  col('year_month')
).groupBy('customer_id').agg(
  min('year_month').alias('first_purchase_month')
)

# Ensure continuity with customer count
print(retail_df.select('customer_id').distinct().count())

display(retail_df_first_purchase_month)

5943


customer_id first_purchase_month null 200912 12346 200912 12347 201010 12348 201009 12349 200912 12350 201102 12351 201011 12352 201011 12353 201010 12354 201104 12355 201005 12356 201010 12357 201011 12358 200912 12359 200912 12360 201002 12361 201001 12362 200912 12363 201104 12364 201108 12365 201102 12366 201003 12367 201112 12368 201003 12369 201003 12370 201002 12371 201003 12372 201102 12373 201002 12374 201004 12375 201109 12376 201010 12377 201004 12378 201005 12379 201006 12380 201002 12381 201108 12382 201001 12383 201012 12384 201108 12385 201011 12386 201012 12387 201010 12388 201005 12389 201002 12390 201109 12391 201002 12392 201004 12393 201010 12394 201105 12395 201004 12396 201002 12397 201107 12398 201110 12399 201003 12400 201010 12401 201102 12402 201002 12403 201007 12404 201001 12405 201107 12406 201001 12407 201103 12408 201007 12409 201005 12410 201007 12411 201010 12412 201006 12413 201011 12414 201009 12415 201006 12416 201002 12417 200912 12418 201003 12419 201010 12420 201110 12421 201007 12422 200912 12423 201008 12424 200912 12425 201009 12426 201002 12427 201012 12428 201103 12429 201006 12430 201110 12431 201001 12432 201106 12433 201008 12434 201011 12435 200912 12436 201109 12437 200912 12438 201107 12439 200912 12440 200912 12441 201012 12442 201112 12443 200912 12444 201106 12445 201010 12446 201110 12447 201104 12448 201110 12449 201009 12450 201008 12451 201006 12452 201111 12453 201107 12454 201001 12455 200912 12456 201103 12457 201009 12458 201008 12459 201004 12460 201009 12461 201107 12462 201102 12463 201104 12464 201102 12465 201106 12466 201001 12467 201010 12468 201001 12469 201006 12470 201001 12471 200912 12472 200912 12473 201106 12474 201002 12475 201010 12476 201007 12477 201003 12478 201112 12479 201111 12480 201007 12481 201004 12482 201002 12483 201001 12484 200912 12485 201006 12486 201010 12487 200912 12488 201109 12489 201101 12490 200912 12491 201111 12492 201011 12493 201105 12494 201005 12495 201003 12496 201003 12497 201001 12498 201110 12499 201005 12500 201002 12501 201101 12502 201102 12503 201005 12504 201004 12505 201010 12506 201104 12507 201005 12508 201111 12509 201102 12510 200912 12511 201010 12512 201110 12513 201108 12514 201003 12515 201012 12516 201004 12517 201106 12518 201108 12519 201008 12520 201103 12521 201107 12522 201110 12523 200912 12524 201002 12525 200912 12526 201109 12527 201006 12528 201101 12529 201006 12530 201003 12531 201001 12532 201111 12533 200912 12534 201108 12535 201106 12536 201110 12537 201010 12538 201011 12539 200912 12540 200912 12541 201103 12542 201003 12543 201009 12544 201111 12545 201103 12546 201109 12547 201007 12548 201106 12549 201001 12550 201109 12551 201012 12552 201110 12553 201010 12554 201009 12555 201001 12556 201107 12557 200912 12558 201112 12559 201101 12560 201107 12561 201102 12562 201009 12563 201010 12564 201103 12565 201102 12566 201109 12567 201002 12568 201003 12569 201104 12570 201001 12571 201108 12572 201110 12573 201008 12574 201101 12575 201007 12576 201007 12577 200912 12578 201009 12579 201109 12580 201005 12581 201110 12582 201005 12583 200912 12584 201103 12585 201012 12586 200912 12587 201112 12588 201004 12589 201001 12590 201004 12591 201010 12592 201007 12593 201105 12594 201003 12595 201007 12596 201104 12597 201103 12598 201003 12599 201005 12600 200912 12601 201010 12602 201110 12603 201111 12604 201103 12605 201009 12606 201001 12607 201110 12608 201010 12609 200912 12610 201108 12611 201110 12612 201109 12613 200912 12614 201103 12615 200912 12616 201011 12617 201111 12618 201111 12619 201005 12620 201105 12621 201002 12622 201104 12623 201001 12624 201106 12625 201004 12626 201101 12627 201107 12628 201110 12629 201010 12630 201110 12631 201001 12632 201005 12633 201007 12634 201006 12635 201009 12636 200912 12637 201006 12638 201003 12639 201003 12640 201109 12641 201108 12642 201108 12643 201004 12644 201001 12645 201002 12646 201110 12647 201001 12648 201001 12649 201001 126

In [0]:
# Join to have original and first purchase dates

retail_df_first_purchase_month =  retail_df.select(
  col('customer_id'),
  col('year_month')
).join(
  retail_df_first_purchase_month,
  on='customer_id',
  how='left'
)

display(retail_df_first_purchase_month.limit(50))


customer_id year_month first_purchase_month 17757 201106 201001 13982 201106 201001 17389 201106 200912 13263 201106 201010 13418 201106 200912 16801 201106 201103 12951 201106 201001 17757 201106 201001 13982 201106 201001 13263 201106 201010 16801 201106 201103 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 17757 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 13982 201106 201001 null 201106 null null 201106 null

In [0]:
# Agg function to add true/false col for whether customer is new or existing
from pyspark.sql.functions import col

def is_new_customer(first_purchase_month, year_month):
  return first_purchase_month == year_month

retail_df_first_purchase_month = retail_df_first_purchase_month.withColumn(
  "is_new_customer",
  is_new_customer(col('first_purchase_month'), col('year_month'))
).withColumn(
  "is_existing_customer",
  ~col('is_new_customer')
)

# Clean Nulls
retail_df_first_purchase_month = retail_df_first_purchase_month.dropna()

display(retail_df_first_purchase_month)

customer_id year_month first_purchase_month is_new_customer is_existing_customer 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13085 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 13078 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 15362 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 18102 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 12682 200912 200912 true false 18087 200912 200912 true false 18087 200912 200912 true false 18087 200912 200912 true false 18087 200912 200912 true false 18087 200912 200912 true false 18087 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 13635 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 14110 200912 200912 true false 12636 200912 

In [0]:
# Aggregate to find total new and total existing customers per month
from pyspark.sql.functions import count, when, col

retail_df_monthly_customers = retail_df_first_purchase_month.groupBy('year_month').agg(
  countDistinct(when(col('is_new_customer') == True, col('customer_id'))).alias('new_customers'),
  countDistinct(when(col('is_existing_customer') == True, col('customer_id'))).alias('existing_customers')
)

display(retail_df_monthly_customers.orderBy('year_month'))

year_month new_customers existing_customers 200912 1045 0 201001 394 392 201002 363 444 201003 436 675 201004 291 707 201005 254 808 201006 269 826 201007 183 805 201008 158 806 201009 242 960 201010 379 1198 201011 322 1361 201012 77 871 201101 71 712 201102 123 675 201103 178 842 201104 105 794 201105 108 971 201106 108 943 201107 102 891 201108 106 874 201109 187 1115 201110 221 1204 201111 192 1519 201112 28 658

Databricks visualization. Run in Databricks to view.

## RFM Tables
We want to use an RFM table to analyse and segment our customer demographics.
Recency, Frequency and Monetary value per customer.

In [0]:
from pyspark.sql.functions import max, datediff, current_date, col, lit, sum

recency_helper = retail_df.agg(max(col('invoice_date'))).collect()[0][0]

# RFM caclculations
rfm_scores = retail_df.groupBy('customer_id').agg(
  datediff(lit(recency_helper), max(col('invoice_date'))).alias('recency'),
  countDistinct("invoice_no").alias("frequency"),
  sum("transaction_total").alias("monetary")
).orderBy('customer_id').dropna()

display(rfm_scores.limit(10))

customer_id recency frequency monetary 12346 325 17 -64.67999999999071 12347 2 8 5633.32 12348 75 5 2019.4 12349 18 5 4404.539999999999 12350 310 1 334.40000000000003 12351 375 1 300.93 12352 36 13 1889.2099999999998 12353 204 2 406.75999999999993 12354 232 1 1079.4 12355 214 2 947.6099999999999

## RFM Segmentation
RFM segmentation categorizes your customers into different segments, according to their interactions with your business, which will allow you to subsequently approach these groups in the most effective way. RFM Segmentation divides customer data into 11 different categories.

We will use our already established RFM table to further create these categories.

In [0]:
from pyspark.sql.functions import when, col, lit

# Create our 5 segments - 20% in each segment
segments = [0.2, 0.4, 0.6, 0.8]
quantiles = rfm_scores.approxQuantile(["recency", "frequency", "monetary"], segments, 0)

# Assign RFM scores to the five segments of customers
rfm_scores = rfm_scores.withColumn(
  "R_Score",
  when(col("recency") < quantiles[0][0], lit(5))
    .when(col("recency") < quantiles[0][1], lit(4))
     .when(col("recency") < quantiles[0][2], lit(3))
      .when(col("recency") < quantiles[0][3], lit(2))
        .otherwise(lit(1))

).withColumn(
  "F_Score",
  when(col("frequency") < quantiles[1][0], lit(1))
   .when(col("frequency") < quantiles[1][1], lit(2))
    .when(col("frequency") < quantiles[1][2], lit(3))
      .when(col("frequency") < quantiles[1][3], lit(4))
        .otherwise(lit(5))
).withColumn(
  "M_Score",
  when(col("monetary") < quantiles[2][0], lit(1))
   .when(col("monetary") < quantiles[2][1], lit(2))
    .when(col("monetary") < quantiles[2][2], lit(3))
      .when(col("monetary") < quantiles[2][3], lit(4))
        .otherwise(lit(5))
)

display(rfm_scores.limit(10))

customer_id recency frequency monetary R_Score F_Score M_Score 12346 325 17 -64.67999999999071 2 5 1 12347 2 8 5633.32 5 4 5 12348 75 5 2019.4 3 4 4 12349 18 5 4404.539999999999 4 4 5 12350 310 1 334.40000000000003 2 2 2 12351 375 1 300.93 2 2 2 12352 36 13 1889.2099999999998 4 5 4 12353 204 2 406.75999999999993 2 2 2 12354 232 1 1079.4 2 2 3 12355 214 2 947.6099999999999 2 2 3

In [0]:
from pyspark.sql.types import StringType
from pyspark.sql.functions import concat

# Calculate combined RFM score
rfm_scores = rfm_scores.withColumn(
  "RFM_ScoreGroup",
  concat(
    col("R_Score").cast(StringType()),
    col("F_Score").cast(StringType()),
    col("M_Score").cast(StringType())
  )
)

display(rfm_scores.limit(10))


customer_id recency frequency monetary R_Score F_Score M_Score RFM_ScoreGroup 12346 325 17 -64.67999999999071 2 5 1 251 12347 2 8 5633.32 5 4 5 545 12348 75 5 2019.4 3 4 4 344 12349 18 5 4404.539999999999 4 4 5 445 12350 310 1 334.40000000000003 2 2 2 222 12351 375 1 300.93 2 2 2 222 12352 36 13 1889.2099999999998 4 5 4 454 12353 204 2 406.75999999999993 2 2 2 222 12354 232 1 1079.4 2 2 3 223 12355 214 2 947.6099999999999 2 2 3 223

In [0]:
from pyspark.sql.functions import regexp_replace

# Segmenting customers according to R and F scores
seg_map = {
  r'[1-2][1-2]': 'Hibernating',
  r'[1-2][3-4]': 'At Risk',
  r'[1-2]5': 'Can\'t Lose',
  r'3[1-2]': 'About to Sleep',
  r'33': 'Need Attention',
  r'[3-4][4-5]': 'Loyal Customers',
  r'41': 'Promising',
  r'51': 'New Customers',
  r'[4-5][2-3]': 'Potential Loyalists',
  r'5[4-5]': 'Champions'
}

rfm_scores = rfm_scores.withColumn(
  "RF_ScoreGroup",
  concat(
    col("R_Score").cast(StringType()),
    col("F_Score").cast(StringType())
  )
)

segment_col = col("RF_ScoreGroup")
for rf, seg in seg_map.items():
  segment_col = when(
    col("RF_ScoreGroup").rlike(rf),
    seg
  ).otherwise(segment_col)

rfm_scores = rfm_scores.withColumn("Segment", segment_col)

display(rfm_scores.limit(10))


customer_id recency frequency monetary R_Score F_Score M_Score RFM_ScoreGroup RF_ScoreGroup Segment 12346 325 17 -64.67999999999071 2 5 1 251 25 Can't Lose 12347 2 8 5633.32 5 4 5 545 54 Champions 12348 75 5 2019.4 3 4 4 344 34 Loyal Customers 12349 18 5 4404.539999999999 4 4 5 445 44 Loyal Customers 12350 310 1 334.40000000000003 2 2 2 222 22 Hibernating 12351 375 1 300.93 2 2 2 222 22 Hibernating 12352 36 13 1889.2099999999998 4 5 4 454 45 Loyal Customers 12353 204 2 406.75999999999993 2 2 2 222 22 Hibernating 12354 232 1 1079.4 2 2 3 223 22 Hibernating 12355 214 2 947.6099999999999 2 2 3 223 22 Hibernating

In [0]:
from pyspark.sql.functions import avg, count

# Finally, find mean and count for each customer segment and score
rfm_scores_summary = rfm_scores.select(
  "Segment",
  "recency",
  "frequency",
  "monetary"
).groupBy("Segment").agg(
  avg("recency").alias("Mean_Recency"),
  avg("frequency").alias("Mean_Frequency"),
  avg("monetary").alias("Mean_Monetary"),
  count("Segment").alias("Count")
)

display(rfm_scores_summary.orderBy("Segment"))

Segment Mean_Recency Mean_Frequency Mean_Monetary Count About to Sleep 106.92572944297082 1.427055702917772 474.3301114058353 377 At Risk 374.8102094240838 4.579842931937173 1147.302748691101 764 Can't Lose 321.0210526315789 16.936842105263157 5384.705915789474 95 Champions 7.16588785046729 23.19392523364486 10423.444889018681 856 Hibernating 466.1025641025641 1.3201840894148587 334.0509875082185 1521 Loyal Customers 65.70397404703974 11.69910786699108 3872.434489862127 1233 Need Attention 111.3359375 3.50390625 1033.03512109375 256 Potential Loyalists 25.292857142857144 2.4357142857142855 728.160095238095 840